In [1]:
import os
import numpy as np
import pandas as pd
import altair as alt
import vega

# Load Data

Dataset 1 : We load data from multiple CSV files; each corresponding to a year from 1999 to 2015. 
Further we have grouped these CSV files into time frames f1, f2, f3 f4 and f5 due to change of format in SAT during these time frames. This makes analysis for every time frame easier.
We concatenate all df's across years to create one single df which is required for few plots.

Dataset 2 : We load geographical data corresponding to every county in California
We combine this data with Dataset 1 as and when needed for analysis

In [2]:
data_path = '../Clean_data/'
# os.listdir(data_path)

In [3]:
def get_data(year, na_values=None):
    '''
    get dataframe of CSV corresponding to given year
    '''
    years = year.split('-')
    f_path = data_path + '/SAT_' + years[0][-2:] + '_' + years[1][-2:] + '.csv'
    df = pd.read_csv(f_path, na_values=na_values)
    df.dropna(inplace=True)
    df['Year'] = year                 ### add corresponding year for every file
    return df

SAT_99_00 = get_data('1999-2000')
SAT_00_01 = get_data('2000-2001')
SAT_01_02 = get_data('2001-2002')
SAT_02_03 = get_data('2002-2003')
SAT_03_04 = get_data('2003-2004')
SAT_04_05 = get_data('2004-2005')
SAT_05_06 = get_data('2005-2006')
SAT_06_07 = get_data('2006-2007')
SAT_07_08 = get_data('2007-2008')
SAT_08_09 = get_data('2008-2009')
SAT_09_10 = get_data('2009-2010')
SAT_10_11 = get_data('2010-2011')
SAT_11_12 = get_data('2011-2012')
SAT_12_13 = get_data('2012-2013')
SAT_13_14 = get_data('2013-2014', na_values='*')
SAT_14_15 = get_data('2014-2015', na_values='*')
SAT_15_16 = get_data('2015-2016', na_values='*')

In [4]:
### DATASET 1
### Create lists of various time frames
f1 = [SAT_99_00, SAT_00_01, SAT_01_02, SAT_02_03, SAT_03_04, SAT_04_05]
f2 = [SAT_05_06, SAT_06_07]
f3 = [SAT_07_08, SAT_08_09, SAT_09_10]
f4 = [SAT_10_11, SAT_11_12, SAT_12_13]
f5 = [SAT_13_14, SAT_14_15, SAT_15_16]


### calculate total scores in time-frame 5
### NOTE: This average score corresponds to average for every school
for df in f5:
    df['Average_Total_Score'] = df['Average_Read_Score'] + df['Average_Math_Score'] + df['Average_Writing_Score']


### add max scores for each year
for df in f1:
    df['Max_score'] = 1600          ### max score from 1999 to 2005 was 1600

for df in f2 + f3 + f4 + f5:
    df['Max_score'] = 2400          ### max score from 1999 to 2005 was 2400


### list of dataframes for all years
f_all = f1 + f2 + f3 + f4 + f5

In [5]:
### calculate Total_School_Score for all the schools across all dataframes i.e. years
### Total_School_Score = Average_Total_Score * Number_of_Takers

for df in f_all:
    df['Total_School_Score'] = df['Average_Total_Score'] * df['Number_of_Takers']

In [6]:
### DATASET 2
df_geo = pd.read_csv('County_GeoPoint.csv')
df_geo.head()

County_Name      TYPE     AREAS   Latitude   Longitude
0        KERN  Suburban  Southern  35.342847 -118.729900
1       KINGS     Rural  Central   36.075360 -119.815503
2  SAN BENITO     Rural  Bay Area  36.605706 -121.074996
3      FRESNO     Urban  Central   36.758180 -119.649323
4      PLUMAS     Rural  Superior  40.004682 -120.838598

In [7]:
### Concatenated dataframe - corresponds to all data available
df_all = pd.concat([df for df in f_all], ignore_index=True)
df_all.shape

(20088, 19)

# Basic Decriptive statistics 

In [8]:
df_all.describe()[['Grade_12_Enrollment','Number_of_Takers','Average_Verbal_Score','Average_Math_Score','Average_Total_Score']]

Grade_12_Enrollment  Number_of_Takers  Average_Verbal_Score  \
count         20088.000000      20088.000000          13234.000000   
mean            319.091348        140.098716            387.638152   
std             229.184788        120.779342            196.494980   
min               0.000000          0.000000              0.000000   
25%             101.000000         39.000000            395.750000   
50%             317.000000        119.000000            465.000000   
75%             488.000000        211.000000            511.000000   
max            1964.000000        848.000000            681.000000   

       Average_Math_Score  Average_Total_Score  
count        20088.000000         20088.000000  
mean           429.851998          1140.099878  
std            174.123906           500.226469  
min              0.000000             0.000000  
25%            425.987500           985.000000  
50%            482.000000          1282.000000  
75%            527.629150          1485.000000  
max            710.300000          2043.000000

In [9]:
df_all.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20088 entries, 0 to 20087
Data columns (total 19 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   County_Name               20088 non-null  object 
 1   District_Name             20088 non-null  object 
 2   School_Name               20088 non-null  object 
 3   Grade_12_Enrollment       20088 non-null  int64  
 4   Number_of_Takers          20088 non-null  int64  
 5   Percent_of_Takers         16401 non-null  float64
 6   Average_Verbal_Score      13234 non-null  float64
 7   Average_Math_Score        20088 non-null  float64
 8   Average_Total_Score       20088 non-null  float64
 9   Number_w/Score_>=1000     7757 non-null   float64
 10  Percent_w/Score_>=1000    7757 non-null   float64
 11  Year                      20088 non-null  object 
 12  Max_score                 20088 non-null  int64  
 13  Total_School_Score        20088 non-null  float64
 14  Averag

# Number of Test-takers and Enrolled-Students across years

In [10]:
df_grp = df_all.groupby(by='Year').sum().reset_index()

melted = pd.melt(df_grp, id_vars=['Year'], value_vars=['Grade_12_Enrollment', 'Number_of_Takers'])
melted['Year'] = melted['Year'].apply(lambda x: x.split('-')[0])

alt.Chart(melted, title='Total_students and Test_takers across years in California').mark_bar().encode(
    column = alt.Column('Year:O', spacing = 5, header = alt.Header(labelOrient = "bottom")),
    x =alt.X('variable', sort = ['Grade_12_Enrollment', 'Number_of_Takers'],  axis=None),
    y =alt.Y('value:Q'),
    color= alt.Color('variable'),
).properties(
    width=38,
    height=250
).configure_axis(
    labelFontSize=12,
    titleFontSize=15
).configure_legend(
  orient='bottom'
)

alt.Chart(...)

Number of SAT takers and Grade-12 students have increased gradually across years. We see that almost 50% of the students enrolled do not take the SAT every year.

# Number of SAT takers per county across years

In [11]:
df_grp = df_all.groupby(['Year','County_Name']).sum().reset_index()

df_grp['Year'] = df_grp['Year'].apply(lambda x: x.split('-')[0])

df_merged = pd.merge(df_grp, df_geo, on='County_Name')  ### Inner join with geographic data


alt.Chart(df_merged).mark_area().encode(
    alt.X('Year:T', axis = alt.Axis(format='%Y',domain=False, tickSize=0)),
    alt.Y('sum(Number_of_Takers):Q', stack='center', axis=None),
    alt.Color('County_Name:N', scale=alt.Scale(scheme='category20c')),
    tooltip=['County_Name:N', 'Average_Total_Score','Number_of_Takers']
).properties(
    title='Streamgraph of Number of test-takers per County Across Years',
    width=800,
    height=450
)

alt.Chart(...)

Los Angeles has highest number of test takers every year. This number is significantly high since it is almost 4 times that of the next highest county.

# Variation of Average_Total_Score across years

In [12]:
df_grp = df_all.groupby(by='Year').sum().reset_index()  ### NOTE: Aggregation alters meaning of columns w.r.t. column names.

df_grp['Average_Score_per_year'] = df_grp['Total_School_Score']/df_grp['Number_of_Takers']

alt.Chart(df_grp, title='Average_Score across years in California').mark_bar(color='#778ba5').encode(
    y = 'Average_Score_per_year',
    x = 'Year'
).properties(
    width=700,
    height=250
).configure_axis(
    labelFontSize=15,
    titleFontSize=15,
)

alt.Chart(...)

We can see a sudden increase in average_total_score 2005-2006 onwards. This calls for a check. We realise that the format of SAT was changed 2005 onwards; writing section was added which took the total marks from 1600 to 2400.

We therefore proceed to plot normalized average scores to look for anomalies.

# Variation of Normalized Total average score across years

In [13]:
df_grp_sum = df_all.groupby(by='Year').sum().reset_index()  ### NOTE: Aggregation alters meaning of columns.
df_grp_sum['Average_Score_per_year'] = df_grp_sum['Total_School_Score'] / df_grp_sum['Number_of_Takers']

df_grp_sum = df_grp_sum[['Year', 'Average_Score_per_year']]

df_grp_avg = df_all.groupby(by='Year').mean().reset_index()[['Year','Max_score']]

df_merged = pd.merge(left=df_grp_sum, right=df_grp_avg , on='Year') ### inner join on Year column
df_merged['Norm_Average_Score'] = df_merged['Average_Score_per_year'] / df_merged['Max_score'] 

In [14]:
alt.Chart(df_merged, title='Normalized Average SAT Score across years in California').mark_bar(color='#bcbd22').encode(
    y = alt.Y('Norm_Average_Score', scale=alt.Scale(domain=[0, 1])),
    x = 'Year'
).properties(
    width=700,
    height=250
).configure_axis(
    labelFontSize=15,
    titleFontSize=15,
)

alt.Chart(...)

Normalized Average score in California has remained almost constant across years.

# Percent of students with Scores >=1500 across years

In [15]:
time_frame = f2 + f3 + f4 + f5 

df_tf = pd.concat([df for df in time_frame], ignore_index=True)  ### concatenate all df's in given timeframe i.e. 2006 - 2015

df_grp = df_tf.groupby(['Year']).sum().reset_index()

df_grp['Percent_w>=1500'] = df_grp['Number_w/Score_>=1500'] * 100 / df_grp['Number_of_Takers']

alt.Chart(df_grp).mark_bar(color='#161e50').encode(
    x=alt.X('Year'),
    y=alt.Y('Percent_w>=1500', scale=alt.Scale(domain=[35,55]), title='% of students' )
).properties(
    title='Percentage of students with Score >= 1500 across years (2005 onwards)',
    width=600,
    height=300)

alt.Chart(...)

There has been a gradual increase in the percent of students till the year 2009-2010. Following this year, there has been a significant decrease in the number till 2016.

# Variation of Average Writing and Math scores across years (2005 onwards) 

In [16]:
time_frame = f2 + f3 + f4 + f5 

for df in time_frame:
    df['Writing_School_Score'] = df['Average_Writing_Score'] * df['Number_of_Takers']
    df['Math_School_Score'] = df['Average_Math_Score'] * df['Number_of_Takers']

df_tf = pd.concat([df for df in time_frame], ignore_index=True)  ### concatenate all df's in given timeframe i.e. 2006 - 2015

df_grp = df_tf.groupby(by='Year').sum().reset_index()  ### NOTE: Aggregation alters meaning of columns.
df_grp['Average_Math_Score_per_year'] = df_grp['Math_School_Score'] / df_grp['Number_of_Takers']
df_grp['Average_Writing_Score_per_year'] = df_grp['Writing_School_Score'] / df_grp['Number_of_Takers']

In [17]:
alt.Chart(df_grp, title="Average Writing and Math scores in California (2005 onwards)").mark_line().encode(
    x=alt.X("Year"),
    y=alt.Y(alt.repeat('layer'), aggregate='mean', title="Scores"
           , scale=alt.Scale(domain=[450, 550])),
    color=alt.ColorDatum(alt.repeat('layer'))
).properties(
    width=400,
    height=350
).repeat(layer=["Average_Math_Score_per_year", "Average_Writing_Score_per_year"]).configure_legend(
  orient='bottom'
)

alt.RepeatChart(...)

The line chart indicates the average Math and Writing scores are constant from 2005 to 2009. In the year 2009-10 there is a spike in these numbers followed by a significant drop in scores from 2010 to 2016.

# Distribution of Average Math and writing scores

In [18]:
time_frame = f2 + f3 + f4 + f5 

for df in time_frame:
    df['Writing_School_Score'] = df['Average_Writing_Score'] * df['Number_of_Takers']
    df['Math_School_Score'] = df['Average_Math_Score'] * df['Number_of_Takers']

df_tf = pd.concat([df for df in time_frame], ignore_index=True)  ### concatenate all df's in given timeframe i.e. 2006 - 2015

In [19]:
alt.data_transformers.enable('default', max_rows=25000) ### increase altair limit

alt.Chart(df_tf).transform_fold(
    ['Average_Math_Score', 'Average_Writing_Score'],
    as_=['Section', 'Score']
).mark_area(
    opacity=0.3,
    interpolate='step'
).encode(
    alt.X('Score:Q', bin=alt.Bin(maxbins=100)),
    alt.Y('count()', stack=None),
    alt.Color('Section:N')
).properties(
    title='Overlapping Histograms for Math and Writing Scores',
    width = 900,
    height = 300
).configure_legend(
  orient='bottom'
)

alt.Chart(...)

We see that the distribution of Math scores is slightly on the higher side than that of the Writing scores. This indicates Most schools in california have higher average Math scores than Writing Scores.

# Variation of Total SAT scores and Number of test takers per county across years   

In [20]:
df_grp = df_all.groupby(by=['Year','County_Name']).sum().reset_index() ### NOTE: Aggr alters meaning ofcolumn names.
df_grp['Average_County_Score'] = df_grp['Total_School_Score'] / df_grp['Number_of_Takers']

df_merged = pd.merge(df_geo, df_grp, on = 'County_Name')

df_merged['Year'] = df_merged['Year'].apply(lambda x: int(x.split('-')[0]))

# df_merged['Number_of_Takers'].max()

In [21]:
select_year = alt.selection_single(
 name='Select', fields=['Year'], init={'Year': 1999},
 bind=alt.binding_range(min=1999, max=2015, step=1)
)

alt.Chart(df_merged).mark_circle(size=60).encode(
    x= alt.X('Longitude', scale=alt.Scale(domain = [df_merged['Longitude'].min()-10, df_merged['Longitude'].max()+10])),
    y= alt.Y('Latitude', scale=alt.Scale(domain = [df_merged['Latitude'].min()-1, df_merged['Latitude'].max()])),
    size = alt.Size('Number_of_Takers', scale=alt.Scale(domain=[-1,4000]), title='Number_of_Takers (Scaled)'),
#     size = 'Number_of_Takers',
    color= alt.Color('Average_County_Score', scale=alt.Scale(scheme='redblue')),
    tooltip=['County_Name','Number_of_Takers', 'Average_County_Score', 'Longitude', 'Latitude']
).add_selection(select_year).transform_filter(select_year).properties(
    width=600,
    height=400
)
# .interactive()

alt.Chart(...)

SAT Scores in the Bay Area seem to be higher as compared to other areas of California.

SAT Scores in the Central region appear comparatively low across years.

Los Angeles has the highest number of test-takers.

Marin had the highest average SAT score from 1999 to 2010, then Santa Clara had the highest average SAT score from 2010 to 2016.

# Variation of Average Scores for Rural, Urban and Suburban areas across years

In [22]:
time_frame = f2 + f3 + f4 + f5 

df_tf = pd.concat([df for df in time_frame], ignore_index=True)  ### concatenate all df's in given timeframe i.e. 2006 - 2015

df_merged = pd.merge(df_tf,df_geo, on = 'County_Name')

df_grp = df_merged.groupby(['Year','TYPE']).sum().reset_index()
df_grp['Average_Type_Score'] = df_grp['Total_School_Score'] / df_grp['Number_of_Takers']

alt.Chart(df_grp).mark_bar().encode(
    x='TYPE',
    y=alt.Y('Average_Type_Score' , scale=alt.Scale(domain=[1400,1600])),
#     y='Average_Type_Score',
    color='TYPE:N',
    column='Year:N'
).configure_legend(
  orient='bottom'
)

alt.Chart(...)

Average scores in Rural areas are slightly higher than in Urban areas.

# Variation of Average SAT scores corresponding to various parts of california across years

In [23]:
df_grp = df_all.groupby(by=['Year','County_Name']).sum().reset_index() ### NOTE: Aggr alters meaning ofcolumn names.
df_grp['Average_County_Score'] = df_grp['Total_School_Score'] / df_grp['Number_of_Takers']

df_merged = pd.merge(df_geo, df_grp, on = 'County_Name')

df_merged['Year'] = df_merged['Year'].apply(lambda x: int(x.split('-')[0]))

# df_merged['Number_of_Takers'].max()

select_year = alt.selection_single(
 name='Select', fields=['Year'], init={'Year': 1999},
 bind=alt.binding_range(min=1999, max=2015, step=1)
)

alt.Chart(df_merged).mark_point(size=60).encode(
    x= alt.X('Longitude', scale=alt.Scale(domain = [df_merged['Longitude'].min()-10, df_merged['Longitude'].max()+10])),
    y= alt.Y('Latitude', scale=alt.Scale(domain = [df_merged['Latitude'].min()-1, df_merged['Latitude'].max()])),
#     size = alt.Size('Number_of_Takers', scale=alt.Scale(domain=[-1,4000])),
#     size = 'Number_of_Takers',
    shape = alt.Size('AREAS' , scale=alt.Scale(zero=False)),
    color= alt.Color('Average_County_Score', scale=alt.Scale(scheme='redblue')),
    tooltip=['County_Name','Number_of_Takers', 'Average_County_Score', 'Longitude', 'Latitude']
).add_selection(select_year).transform_filter(select_year).properties(
    width=600,
    height=400
)
# .interactive()

alt.Chart(...)

Counties in Bay Area have higher average SAT scores as compared to other regions

Counties located in the Southern region towards the coast have higher average scores as compared to those which are away from coast

Most of the counties in the Superior region have average scores which are neither too low nor too high


We plot Joint-bar-graphs to better visualize the scores across time

In [24]:
time_frame = f2 + f3 + f4 + f5 

df_tf = pd.concat([df for df in time_frame], ignore_index=True)  ### concatenate all df's in given timeframe i.e. 2006 - 2015

df_merged = pd.merge(df_tf,df_geo, on = 'County_Name')

df_grp = df_merged.groupby(['Year','AREAS']).sum().reset_index()
df_grp['Average_Area_Score'] = df_grp['Total_School_Score'] / df_grp['Number_of_Takers']

alt.Chart(df_grp).mark_bar().encode(
    x='AREAS',
    y=alt.Y('Average_Area_Score' , scale=alt.Scale(domain=[1350,1650])),
#     y='Average_Type_Score',
    color='AREAS:N',
    column='Year:N'
).configure_legend(
  orient='bottom'
).properties(
    width=80,
    height=200
)
# .interactive()

alt.Chart(...)

This clearly shows that Average scores in Bay Area is higher as compared to other areas.

# Supplementary Information

Link to Presentation Video : https://youtu.be/jhPsmnHSe7w

Data files - 'SAT_00_01.csv',
             'SAT_01_02.csv',
             'SAT_02_03.csv',
             'SAT_03_04.csv',
             'SAT_04_05.csv',
             'SAT_05_06.csv',
             'SAT_06_07.csv',
             'SAT_07_08.csv',
             'SAT_08_09.csv',
             'SAT_09_10.csv',
             'SAT_10_11.csv',
             'SAT_11_12.csv',
             'SAT_12_13.csv',
             'SAT_13_14.csv',
             'SAT_14_15.csv',
             'SAT_15_16.csv',
             'SAT_99_00.csv',
             'County_GeoPoint.csv'
             
Description of SAT changes over years - 'SAT_Changes.xlsx'